In [1]:
import os
import sys
#sys.path.append('/home/wayve/prajwal/pixtrack/')
import cv2
import pycolmap
from hloc.utils import viz_3d
import numpy as np
import pixtrack.utils.pose_utils as pose_utils
from pixloc.utils.colmap import Camera as ColCamera
from pixloc.pixlib.geometry import Camera as PixCamera, Pose
import matplotlib.pyplot as plt
import plotly.express as px
import torch
import kornia
import einops

In [2]:
sfm_path = '/home/wayve/prajwal/pixtrack/data/pixtrack/objects/003_cracker_box/pixtrack/aug_nerf_sfm/ref/'
model = pycolmap.Reconstruction(sfm_path)
#sfm_path2 = '/data/pixtrack/objects/003_cracker_box/pixtrack/pixsfm/outputs/ref/'
#model2 = pycolmap.Reconstruction(sfm_path2)
fig = viz_3d.init_figure()
viz_3d.plot_reconstruction(fig, model, color='rgba(0,255,0,0.5)', name="low_res", cameras=True, cs=.025)
#viz_3d.plot_reconstruction(fig, model2, color='rgba(255,0,0,0.5)', name="high_res", cameras=True, cs=.05)
fig.show()

In [3]:
import cv2
import matplotlib.pyplot as plt
from pixtrack.visualization.run_vis_on_poses import get_nerf_image
from pixtrack.utils.pose_utils import get_world_in_camera_from_pixpose, get_camera_in_world_from_colmap_image, rotate_image, get_camera_in_world_from_pixpose, get_camera_in_world_from_colmap_image
from pixtrack.utils.ingp_utils import load_nerf2sfm, initialize_ingp, sfm_to_nerf_pose, nerf_to_sfm_pose, get_nerf_aabb_from_sfm
from pixloc.pixlib.geometry import Pose, Camera as PixCamera
from hloc.utils.read_write_model import Camera as ColCamera
import pycolmap

In [4]:
nerf_path = '/data/pixtrack/objects/003_cracker_box/pixtrack/instant-ngp/snapshots/weights.msgpack'
nerf2sfm_path = '/data/pixtrack/objects/003_cracker_box/pixtrack/pixsfm/dataset/nerf2sfm.pkl'
nerf2sfm = load_nerf2sfm(nerf2sfm_path)
aabb = get_nerf_aabb_from_sfm(os.path.join(sfm_path), nerf2sfm_path)
testbed = initialize_ingp(str(nerf_path), aabb)

00:42:52 INFO     Loading network config from: /data/pixtrack/objects/003_cracker_box/pixtrack/instant-ngp/snapshots/weights.msgpack
00:42:52 INFO     GridEncoding:  Nmin=16 b=1.51572 F=2 T=2^19 L=16
00:42:52 INFO     Density model: 3--[HashGrid]-->32--[FullyFusedMLP(neurons=64,layers=3)]-->1
00:42:52 INFO     Color model:   3--[Composite]-->16+16--[FullyFusedMLP(neurons=64,layers=4)]-->3
00:42:52 INFO       total_encoding_params=13074912 total_network_params=10240


In [5]:
W = model.cameras[1].width
H = model.cameras[1].height
f, cx, cy, _ = model.cameras[1].params
intrinsics = np.array([[f, 0, cx], [0, f, cy], [0, 0, 1]])
col_camera = ColCamera(
        id=1,
        model="OPENCV",
        width=W,
        height=H,
        params=np.array([f, f, cx, cy]),
    )
cIw = get_camera_in_world_from_colmap_image(model.images[1])
nerf_pose = sfm_to_nerf_pose(nerf2sfm, cIw)
ref_camera = PixCamera.from_colmap(col_camera)


In [6]:
normals = get_nerf_image(testbed, 
                        nerf_pose, 
                        ref_camera, 
                        depth=True)

In [7]:
normals

array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)

In [ ]:
def draw_points(norm_img, pts):
    for pt in pts:
        #print(pt)
        norm_img = cv2.circle(norm_img, 
               center=(int(pt[0]), int(pt[1])), 
               radius=10,
               color=(0, 255, 0),
               thickness=3,
              )
    return norm_img

In [1]:
intrinsics

NameError: name 'intrinsics' is not defined

In [ ]:
normals = kornia.geometry.depth.depth_to_normals(
            camera_matrix=torch.Tensor(intrinsics).unsqueeze(0), 
            depth=depth_img.unsqueeze(0).unsqueeze(0))[0]

norm_rea = einops.rearrange(normals, 'c h w -> h w c')
norm_img = np.array((norm_rea.numpy().copy() * 255).astype(np.uint8))

pts_np = np.array([point.xy for point in model.images[1].points2D 
                   if point.point3D_id != 18446744073709551615])
norm_img = draw_points(norm_img, pts_np)

In [ ]:
px.imshow(norm_img)

In [ ]:
pts = torch.tensor(pts_np)
pts = pts[None]
normals = normals[None]
scale = torch.tensor([W-1, H-1]).to(pts)
pts = (pts / scale) * 2 - 1
pts = pts.clamp(min=-1, max=1)  # ideally use the mask instead
interpolated = torch.nn.functional.grid_sample(
                normals.float(), 
                pts[:, None].float(), 
                mode='bilinear', 
                align_corners=True)
interpolated = interpolated.squeeze()

In [ ]:
pts_3d = [model.points3D[pt.point3D_id].xyz 
          for pt in model.images[1].points2D 
          if pt.point3D_id != 18446744073709551615]
pts_3d = np.array(pts_3d)

In [ ]:
fig = go.Figure(data = go.Scatter3d(
        x=pts_3d[:, 0], y=pts_3d[:, 1], z=pts_3d[:, 2], mode='markers',
        marker=dict(
            size=2, 
            color='rgba(255, 0, 0, 1)', 
            line_width=0.0, 
            colorscale=None)))

fig.update_layout(scene=dict(aspectmode='data',
                             camera_eye=dict(x=1.2, y=1.2, z=0.6)))

fig.show()

In [ ]:
import plotly.graph_objects as go
import pandas as pd

fig = go.Figure(data = go.Cone(
    x=pts_3d[:, 0],
    y=pts_3d[:, 1],
    z=pts_3d[:, 2],
    u=interpolated[1, :],
    v=interpolated[2, :],
    w=interpolated[0, :],
    colorscale='Blues',
    sizemode="absolute",
    sizeref=40))

fig.update_layout(scene=dict(aspectmode='data',
                             camera_eye=dict(x=1.2, y=1.2, z=0.6)))

fig.show()

In [ ]:
import einops


In [ ]:
import PIL

In [ ]:
fig = px.imshow(norm_img)
fig.show()

In [ ]:
pts = [point.xy for point in model.images[1].points2D]

In [ ]:
pts = np.array(pts)

In [ ]:
px.imshow(nerf_img)

In [ ]:
xyzs = np.array([p3D.xyz for _, p3D in model2.points3D.items()])

In [ ]:
sfm_path = '/data/pixtrack/objects/006_mustard_bottle/pixtrack/pixsfm/outputs/ref/'
model = pycolmap.Reconstruction(sfm_path)
#sfm_path2 = '/data/pixtrack/objects/003_cracker_box/pixtrack/pixsfm/outputs/ref/'
#model2 = pycolmap.Reconstruction(sfm_path2)
fig = viz_3d.init_figure()
viz_3d.plot_reconstruction(fig, model, color='rgba(0,255,0,0.5)', name="low_res", cameras=True, cs=.05)
#viz_3d.plot_reconstruction(fig, model2, color='rgba(255,0,0,0.5)', name="high_res", cameras=True, cs=.05)
fig.show()

In [ ]:
import os
os.environ['OBJ_AABB'] = "[[0., 0., 0.], [1., 1., 1.]]"
from pixtrack.utils.ingp_utils import load_nerf2sfm, sfm_to_nerf_pose

In [ ]:
def get_nerf_aabb_from_sfm(sfm_path, nerf2sfm_path):
    nerf2sfm = load_nerf2sfm(nerf2sfm_path)
    model = pycolmap.Reconstruction(sfm_path)
    points3d_in_nerf = []
    for point in model.points3D:
        pose_placeholder = np.eye(4)
        pose_placeholder[:3, -1] = model.points3D[point].xyz
        pose_placeholder_nerf = sfm_to_nerf_pose(nerf2sfm=nerf2sfm, sfm_pose=pose_placeholder)[:3, -1]
        points3d_in_nerf.append(pose_placeholder_nerf)
    points3d_in_nerf = np.array(points3d_in_nerf)
    min_xyz = points3d_in_nerf.min(axis=0)
    max_xyz = points3d_in_nerf.max(axis=0)
    min_bounds = min_xyz / 3. + np.array([0.5, 0.5, 0.5])
    max_bounds = max_xyz / 3. + np.array([0.5, 0.5, 0.5])
    aabb_bounds = [min_bounds.tolist(), max_bounds.tolist()]
    return aabb_bounds, points3d_in_nerf


In [ ]:
sfm_path = '/data/pixtrack/objects/006_mustard_bottle/pixtrack/pixsfm/outputs/ref/'
nerf2sfm_path = '/data/pixtrack/objects/006_mustard_bottle/pixtrack/pixsfm/dataset/nerf2sfm.pkl'

In [ ]:
nerf2sfm = load_nerf2sfm(nerf2sfm_path)

In [ ]:
aabb, points3d_in_nerf = get_nerf_aabb_from_sfm(sfm_path, nerf2sfm_path)

In [ ]:
np.min(points3d_in_nerf, axis=0) / 3.

In [ ]:
pcd = o3d.geometry.PointCloud()
pcd.points = o3d.utility.Vector3dVector(xyzs)
o3d.io.write_point_cloud("cracker_box.ply", pcd)

In [ ]:
sfm_path = '/data/pixtrack/objects/003_cracker_box/old_pixtrack/nerf_sfm/sfm/'
model = pycolmap.Reconstruction(sfm_path)
sfm_path2 = '/data/pixtrack/objects/003_cracker_box/pixtrack/nerf_sfm/sfm/'
model2 = pycolmap.Reconstruction(sfm_path2)
fig = viz_3d.init_figure()
viz_3d.plot_reconstruction(fig, model, color='rgba(0,255,0,0.5)', name="low_res", cameras=True, cs=.5)
viz_3d.plot_reconstruction(fig, model2, color='rgba(255,0,0,0.5)', name="high_res", cameras=True, cs=.05)
fig.show()

In [ ]:
sfm_path = '/data/pixtrack/outputs/nerf_sfm/aug_003_cracker_box/sfm/'
model = pycolmap.Reconstruction(sfm_path)
fig = viz_3d.init_figure()
viz_3d.plot_reconstruction(fig, model, color='rgba(0,255,0,0.5)', name="reference", cameras=True, cs=0.125/4)
fig.show()

In [ ]:
{model.images[x] for x in model.images if '96' in model.images[x].name}

In [ ]:
sfm_path = '/data/pixtrack/outputs/nerf_sfm/aug_003_cracker_box/aug_sfm/'
model = pycolmap.Reconstruction(sfm_path)
fig = viz_3d.init_figure()
viz_3d.plot_reconstruction(fig, model, color='rgba(0,255,0,0.5)', name="reference", cameras=True, cs=0.125/4)
fig.show()

In [ ]:
from pixtrack.utils.ingp_utils import load_nerf2sfm, initialize_ingp, sfm_to_nerf_pose
from pixtrack.visualization.run_vis_on_poses import get_nerf_image
nerf_path = '/home/prajwal.chidananda/code/pixtrack/instant-ngp/snapshots/gimble_04MAR2022/weights.msgpack'
nerf2sfm_path = '/home/prajwal.chidananda/code/pixtrack/instant-ngp/data/nerf/gimble_04MAR2022/nerf2sfm.pkl'
nerf2sfm = load_nerf2sfm(nerf2sfm_path)
testbed = initialize_ingp(nerf_path)

In [ ]:
camera = model.cameras[1]
camera = ColCamera(None, 
                camera.model_name,
                int(camera.width),
                int(camera.height),
                camera.params)
camera = PixCamera.from_colmap(camera)

In [ ]:
image = model.images[165]
cIw = pose_utils.get_camera_in_world_from_colmap_image(image)
nerf_pose = sfm_to_nerf_pose(nerf2sfm, cIw)
nerf_img = get_nerf_image(testbed, nerf_pose, camera)
plt.imshow(nerf_img)

In [ ]:
path = os.path.join('../outputs/nerf_sfm/aug_gimble_04MAR2022/', image.name)
img = cv2.imread(path, -1)
plt.imshow(img)